Model Fitting Data Generation

Libraries and Functions

In [1]:
import numpy as np
import matplotlib.pyplot as plt
from numpy import random
import scipy.stats
from scipy.stats import t
import pandas as pd

def linear_regression(x, y, prob):
    """
    Return the linear regression parameters and their <prob> confidence intervals.
    ex:
    >>> linear_regression([.1,.2,.3],[10,11,11.5],0.95)
    """
    x = np.array(x)
    y = np.array(y)
    n = len(x)
    xy = x * y
    xx = x * x

    # estimates

    b1 = (xy.mean() - x.mean() * y.mean()) / (xx.mean() - x.mean()**2)
    # b0 = y.mean() - b1 * x.mean()
    # s2 = 1./n * sum([(y[i] - b0 - b1 * x[i])**2 for i in range(n)])
    b0 = y.mean()
    s2 = 1./n * sum([(y[i] - b0)**2 for i in range(n)])
    #print('b0 = ',b0)
    #print('b1 = ',b1)
    #print 's2 = ',s2
    
    #confidence intervals
    
    alpha = 1 - prob
    c1 = scipy.stats.chi2.ppf(alpha/2.,n-2)
    c2 = scipy.stats.chi2.ppf(1-alpha/2.,n-2)
    #print('the confidence interval of s2 is: ',[n*s2/c2,n*s2/c1])
    
    c = -1 * scipy.stats.t.ppf(alpha/2.,n-2)
    bb1 = c * (s2 / ((n-2) * (xx.mean() - (x.mean())**2)))**.5
    #print('the confidence interval of b1 is: ',[b1-bb1,b1+bb1])
    
    #bb0 = c * ((s2 / (n-2)) * (1 + (x.mean())**2 / (xx.mean() - (x.mean())**2)))**.5
    bb0 = c * ((s2 / (n-2)))**.5
    #print('the confidence interval of b0 is: ',[b0-bb0,b0+bb0])
    return [b0, bb0]

def conf_intervals(x, prob):
    m = x.mean() 
    s = x.std() 
    dof = len(x)-1 

    t_crit = np.abs(t.ppf((1-prob)/2,dof))

    return [m-s*t_crit/np.sqrt(len(x)), m+s*t_crit/np.sqrt(len(x))]

Pilot Study

In [ ]:
parts = ["acc", "est"]
fakes = ["t", "b", "c_u", "c_d", "o_u", "o_d"]
number_points = 100
conf = 0.95

means = list()
std_dev = list()
box_sizes = list()
value_max = list()
value_min = list()
fakes_list = list()
fake_means = list()
conf_u = list()
conf_d = list()


for fake in fakes:
    for i in range(1,6):
        ##generate x-coordinates
        x = random.randint(0, 100, size = number_points)

        ##random box and mean
        box_min = random.randint(0, 50)
        box_size = random.randint(50, 100)
        box_max = min(box_min + box_size, 100)

        true_mean = random.randint(box_min + 20, box_max - 20)

        ##generating data
        alpha = 1
        beta = (alpha*(box_max-true_mean))/(true_mean-box_min)  #calculating beta (from (max-min)*alpha/(alpha+beta)+min = mean) with alpha fix
        y = (box_max-box_min) * random.beta(a = alpha, b = beta, size = number_points) + box_min  #generating values from beta distribution for fixed range

        ##mean shifting
        y = y - np.mean(y) #dat with zero mean
        y = y + true_mean #getting predefined mean
        for j in range(len(y)):
            if y[j] > 100:
                y[j] = box_max
            elif y[j] < 0:
                y[j] = box_min

        ##calculating the regression
        [b0, bb0] = linear_regression(x,y,conf)
        regr = b0  #+ b1* range(1,101)
        conf_min = b0-bb0 #+ (b1-bb1) * range(1,101)
        conf_max = b0+bb0 #+ (b1+bb1) * range(1,101)

        ##plotting
        for part in parts:

            if part == "acc":
                if fake == "t":
                    fake_mean = np.mean(y)
                elif fake == "b":
                    fake_mean = np.min(y) + (np.max(y) - np.min(y))/2
                elif fake == "c_u":
                    fake_mean = conf_max
                elif fake == "c_d":
                    fake_mean = conf_min
                elif fake == "o_u":
                    fake_mean = conf_max + random.randint(0, 5)
                elif fake == "o_d":
                    fake_mean = conf_min - random.randint(0, 5)

            ##storing statistics
            if part == "acc":
                means.append(np.mean(y))
                std_dev.append(np.std(y))
                value_max.append(np.max(y))
                value_min.append(np.min(y))
                box_sizes.append(np.max(y) - np.min(y))
                fakes_list.append(fake + "_" + str(i))
                fake_means.append(fake_mean)
                conf_u.append(conf_max)
                conf_d.append(conf_min) 

            plt.figure(figsize=(8, 7))
            plt.scatter(x, y, s = 20, linewidths=0, color = "black")
            if part == "acc":
                plt.plot(range(1,101), np.full((100,1), fake_mean), color = "red")
            plt.xlim([-1,101])
            plt.ylim([-1,101])
            plt.xticks([])
            plt.yticks([])

            #plt.savefig("Pilot_Vis/" + str(part) + "_" + str(fake) + "_" + str(i) + ".png", format = "png", dpi = 300, bbox_inches='tight')
    #std_dev_mean.append(np.mean(std_dev))

#print(np.mean(std_dev_mean))

#data_stats = pd.DataFrame(data = {'fake': fakes_list,"mean": means,"fake_mean": fake_means, "std_dev":std_dev, "value_min": value_min, "value_max": value_max, "box_size": box_sizes, "conf_max": conf_u, "conf_min": conf_d})
#data_stats.to_csv("data_stats.csv")

Main Study

In [ ]:
parts = ["val", "est"]
errors_u = np.linspace(0, 0.7, 25)
errors_d = np.linspace(-0.7, 0, 25)
fakes = list()
for direction in ["u", "d"]:
    for i in range(0,25):
        fakes.append(direction + "_" + str(i))
number_points = 100
conf = 0.95

means = list()
medians = list()
std_devs = list()
relative_variances = list()
box_sizes = list()
value_max = list()
value_min = list()
points_above = list()
points_below = list()
fakes_list = list()
fake_means = list()
conf_u = list()
conf_d = list()

for fake in fakes:
    for i in range(1,2):
        ##generate x-coordinates
        x = random.randint(0, 100, size = number_points)

        ##box size and random mean
        box_min = 10
        box_max = 90

        true_mean = random.randint(30, 70)
        true_std_dev = random.randint(15, 25)
        
        above = 0
        below = 0

        while abs(above-below) < 10:

            ##generating data
            y = random.normal(loc=true_mean, scale=true_std_dev, size=number_points) #normal distribution

            ##mean shifting
            y = y - np.mean(y) #dat with zero mean
            y = y + true_mean #getting predefined mean
            for j in range(len(y)):
                if y[j] > 100:
                    y[j] = box_max
                elif y[j] < 0:
                    y[j] = box_min

            ##number of points above/below mean
            above = 0
            below = 0
            for value in y:
                if value >= np.mean(y):
                    above = above + 1
                else: below = below + 1

        ##plotting
        for part in parts:

            if part == "val":

                [conf_min, conf_max] = conf_intervals(y, conf)

                ##shown mean
                if "u_" in fake:
                    fake_mean = np.mean(y) + errors_u[int(fake[2:])]*np.std(y)
                    relative_variances.append(errors_u[int(fake[2:])])
                elif "d_" in fake:
                    fake_mean = np.mean(y) + errors_d[24-int(fake[2:])]*np.std(y)
                    relative_variances.append(errors_d[24-int(fake[2:])])

                ##storing statistics
                means.append(round(np.mean(y),2))
                medians.append(round(np.median(y),2))
                std_devs.append(round(np.std(y),2))
                value_max.append(round(np.max(y),2))
                value_min.append(round(np.min(y),2))
                points_above.append(above)
                points_below.append(below)
                box_sizes.append(round(np.max(y) - np.min(y),2))
                fakes_list.append(fake)
                fake_means.append(round(fake_mean,2))
                conf_u.append(round(conf_max,2))
                conf_d.append(round(conf_min,2))

                ##save data
                #raw_data = pd.DataFrame(data = {"x": x, "y": y})
                #raw_data.to_csv("Study_Data/" + str(fake) + ".csv")

            plt.figure(figsize=(8, 7))
            plt.scatter(x, y, s = 20, linewidths=0, color = "black")
            if part == "val":
                plt.plot(range(1,101), np.full((100,1), fake_mean), color = "red")
            plt.xlim([-1,101])
            plt.ylim([-1,101])
            plt.xticks([])
            plt.yticks([])

            ##plot
            #plt.savefig("Study_Vis/" + str(part) + "_" + str(fake) + ".png", format = "png", dpi = 300, bbox_inches='tight')

#data_stats = pd.DataFrame(data = {'fake': fakes_list,"mean": means, "median": medians, "std_dev": std_devs, "fake_mean": fake_means, "relative_variance": relative_variances, "value_min": value_min, "value_max": value_max, "box_size": box_sizes, "conf_max": conf_u, "conf_min": conf_d, "points_above": points_above, "points_below": points_below})
#data_stats.to_csv("data_stats.csv")